In [1]:
import random
import numpy as np
import scanpy as sc
import anndata as an
import scipy.stats as st
from scipy.spatial import KDTree
import math

In [2]:
def LoadData(path):
    adata = sc.read_visium(path)
    adata.var_names_make_unique()
    return adata

In [3]:
path ="/Users/juliafoyer/Documents/Skolarbete/Masters_thesis/human_breast_cancer_ST_data"
adata = LoadData(path)

Variable names are not unique. To make them unique, call `.var_names_make_unique`.
Variable names are not unique. To make them unique, call `.var_names_make_unique`.


In [4]:
adata

AnnData object with n_obs × n_vars = 3798 × 36601
    obs: 'in_tissue', 'array_row', 'array_col'
    var: 'gene_ids', 'feature_types', 'genome'
    uns: 'spatial'
    obsm: 'spatial'

In [5]:
spots = adata.obs_names
genes = adata.var_names
n_spots = len(adata.obs_names)
n_genes = len(adata.var_names)

In [6]:
print(spots)
print(genes)
print(n_spots)
print(n_genes)

Index(['AAACAAGTATCTCCCA-1', 'AAACACCAATAACTGC-1', 'AAACAGAGCGACTCCT-1',
       'AAACAGGGTCTATATT-1', 'AAACAGTGTTCCTGGG-1', 'AAACATTTCCCGGATT-1',
       'AAACCCGAACGAAATC-1', 'AAACCGGGTAGGTACC-1', 'AAACCTAAGCAGCCGG-1',
       'AAACCTCATGAAGTTG-1',
       ...
       'TTGTGGTAGGAGGGAT-1', 'TTGTGGTGGTACTAAG-1', 'TTGTGTATGCCACCAA-1',
       'TTGTTAGCAAATTCGA-1', 'TTGTTCAGTGTGCTAC-1', 'TTGTTGTGTGTCAAGA-1',
       'TTGTTTCACATCCAGG-1', 'TTGTTTCATTAGTCTA-1', 'TTGTTTCCATACAACT-1',
       'TTGTTTGTGTAAATTC-1'],
      dtype='object', length=3798)
Index(['MIR1302-2HG', 'FAM138A', 'OR4F5', 'AL627309.1', 'AL627309.3',
       'AL627309.2', 'AL627309.5', 'AL627309.4', 'AP006222.2', 'AL732372.1',
       ...
       'AC133551.1', 'AC136612.1', 'AC136616.1', 'AC136616.3', 'AC136616.2',
       'AC141272.1', 'AC023491.2', 'AC007325.1', 'AC007325.4', 'AC007325.2'],
      dtype='object', length=36601)
3798
36601


In [6]:
def assign_random(adata, K):
    n_spots = len(adata.obs_names)
    n_genes = len(adata.var_names)
    gene_factor = np.zeros((n_spots, n_genes))
    for spot in range(n_spots):
        spot_gene_factor = np.zeros(n_genes)
        for gene in range(n_genes):
            spot_gene_factor[gene] = np.random.randint(0, K)
        gene_factor[spot] = spot_gene_factor
    return gene_factor

In [7]:
gene_factor = assign_random(adata, 3)

In [8]:
# Factors assigned randomly to each gene (columns) for all spots (rows).
gene_factor

array([[2., 2., 1., ..., 1., 1., 0.],
       [1., 1., 1., ..., 1., 1., 0.],
       [2., 0., 2., ..., 1., 1., 1.],
       ...,
       [1., 2., 2., ..., 0., 0., 0.],
       [0., 1., 0., ..., 1., 1., 1.],
       [0., 0., 0., ..., 0., 2., 1.]])

In [30]:
gene_factor.shape

(3798, 36601)

In [9]:
def count_gene_factor(gene_factor, K):
    gene_factor_count = np.zeros((K, len(gene_factor[1,:])))
    for factor in range(K):
        count = np.count_nonzero(gene_factor == factor, axis = 0)
        gene_factor_count[factor] = count
    return gene_factor_count

In [10]:
gene_factor_count = count_gene_factor(gene_factor, 3)

In [11]:
# How many times (across all spots) is each and every gene (columns) assigned to each factor (rows).
gene_factor_count

array([[1260., 1210., 1250., ..., 1284., 1241., 1290.],
       [1201., 1312., 1287., ..., 1252., 1238., 1263.],
       [1337., 1276., 1261., ..., 1262., 1319., 1245.]])

In [12]:
gene_factor_count.shape

(3, 36601)

In [22]:
def count_spot_factor(gene_factor, K):
    spot_factor_count = np.zeros((len(gene_factor), K))
    for factor in range(K):
        count = np.count_nonzero(gene_factor == factor, axis = 1)
        spot_factor_count[:,factor] = count
    return spot_factor_count

In [23]:
spot_factor_count = count_spot_factor(gene_factor, 3)

In [24]:
# For each spot (rows), how many genes are assigned to each and every factor (columns).
spot_factor_count

array([[12388., 12089., 12124.],
       [12078., 12263., 12260.],
       [12128., 12227., 12246.],
       ...,
       [12164., 12203., 12234.],
       [12160., 12304., 12137.],
       [12285., 12241., 12075.]])

In [31]:
spot_factor_count.shape

(3798, 3)

In [38]:
# Get a theta for now...
K = 3
dist_g = lambda x: np.random.dirichlet(x)
alpha = 0.1 * np.ones(K)
theta = np.zeros((n_spots, K))
for row in range(n_spots):
    theta[row] = dist_g(alpha)
print(theta)

[[9.10143889e-01 1.75042788e-12 8.98561112e-02]
 [5.96517900e-08 8.40907765e-12 9.99999940e-01]
 [4.72150209e-05 4.41596365e-12 9.99952785e-01]
 ...
 [5.10629726e-26 4.06653306e-02 9.59334669e-01]
 [8.04845103e-02 9.19509113e-01 6.37646531e-06]
 [3.28646866e-09 8.17630124e-17 9.99999997e-01]]


In [47]:
def get_phi(gene_factor_count):
    phi = np.zeros((K, n_genes))
    for factor in range(K):
        for gene in range(n_genes):
            phi[factor, gene] = gene_factor_count[factor, gene]/np.sum(gene_factor_count, axis=1)[factor]
    return phi

In [48]:
phi = get_phi(gene_factor_count)

In [49]:
phi

array([[2.71900548e-05, 2.61110844e-05, 2.69742607e-05, ...,
        2.77079606e-05, 2.67800460e-05, 2.78374370e-05],
       [2.59210554e-05, 2.83167566e-05, 2.77771842e-05, ...,
        2.70217830e-05, 2.67196225e-05, 2.72591948e-05],
       [2.88537476e-05, 2.75373089e-05, 2.72135945e-05, ...,
        2.72351754e-05, 2.84652903e-05, 2.68682990e-05]])

In [34]:
def Gibbs(gene_factor, gene_factor_count, spot_factor_count, K, iterations, beta = 0.1):
    for it in range(iterations):
#        for spot in gene_factor[:,:]:
        for spot in range(len(gene_factor)):
#            for gene in spot:
            for gene in range(len(gene_factor[1,:])):
                # Calculate probability of factor
                left = theta[spot, factor]
                right = phi[]

In [35]:
Gibbs(gene_factor, gene_factor_count, spot_factor_count, 3, 3)

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

...

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.00401985 0.80163513]
[0.19434502 0.004019

KeyboardInterrupt: 